In [2]:
import os
from project import Project 
from functions import *

/anaconda/envs/xaienv/lib/python3.9/site-packages/statsmodels/compat/pandas.py:61: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import Int64Index as NumericIndex


In [3]:

ant_project = Project('ANT')
ant_project.set_train_test()
ant_project.prepare_data()
ant_project.get_sampled_data()
# Train model for ANT 
ant_project.train_global_model('SVM')
global_model = ant_project.models['SVM']

X_test = ant_project.X_test
y_test = ant_project.y_test
X_train = ant_project.X_train_rs
y_train = ant_project.y_train_rs
project_name = ant_project.name
# TODO change to not resampled data

In [4]:
limeExp,lime_explanations = get_explanations(project_name, 'lime','SVM',X_train,y_train,global_model )

In [5]:
pyExp,pyexplanations = get_explanations(project_name, 'pyExp','SVM',X_train,y_train,global_model )

In [6]:
shapExp,shap_explanations = get_explanations(project_name, 'shap','SVM',X_train,y_train,global_model )

X does not have valid feature names, but SVC was fitted with feature names
Using 518 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


Show Examples of explanation

In [7]:
index = 3
lime_example = lime_explanations[index]
py_example = pyexplanations[index]
shap_example = shap_explanations[index]

X_explain = ant_project.test_data_x.iloc[index]
y_explain = ant_project.test_data_y.iloc[index]

In [16]:
np.set_printoptions(precision=2,suppress=True)

In [8]:
# lime explanation
print(lime_example.keys())
print("Instance of interest: ", lime_example['name'])
lime_example['rule'].show_in_notebook(show_table=True)

dict_keys(['rule', 'synthetic_instance_for_global_model', 'synthetic_instance_for_local_model', 'local_model', 'selected_feature_indices', 'name'])
Instance of interest:  org.apache.tools.ant.util.FileUtils


In [92]:
top_relevant_features = []
exp = lime_example['rule']
imps = [np.abs(exp.as_list()[i][1] )for i in range(len(exp.as_list()))  ]
boundary = np.quantile(imps, .75)
print(boundary)
for i,imp in exp.as_map()[1]:
    if imp < boundary:
        break
    # print(i,imp)
    top_relevant_features.append((i,imp))
# print(exp.as_map()[1])
# print(top_relevant_features)
print()

from operator import itemgetter
coef_map = sorted(exp.as_map()[1],key=itemgetter(0))
ori = [np.abs(exp.as_map()[1][i][0]) for i in range(len(exp.as_map()[1]))]
# ori = np.array(ori[::-1])
for ind in np.nditer(np.array(ori[::-1])):
    print(ind)
# [ print(map[i][0]) for i in range(len(map)) if (map[i][0] == i) ]
# print(lime_example['selected_feature_indices'])

0.022879674510674693

8
9
2
7
18
0
16
4
5
10


In [102]:
print(exp.as_list()[0][0])

loc > 543.00


In [8]:
# shap explanation
import shap
shap.initjs()
print(shap_example.keys())
print("Instance of interest: ", shap_example['name'])
shap.force_plot(shapExp.expected_value,shap_example['shap_values'],X_explain,link="logit")

dict_keys(['name', 'shap_values'])
Instance of interest:  org.apache.tools.ant.util.FileUtils


In [11]:
all_shap_values = shapExp.shap_values(ant_project.test_data_x,nsamples=2000, l1_reg="num_features(10)")

  0%|          | 0/100 [00:00<?, ?it/s]

X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid fea

In [ ]:
shap.force_plot(shapExp.expected_value,all_shap_values,ant_project.test_data_x)

In [47]:
coefs_shap = np.array(shap_example['shap_values'])
count = np.count_nonzero(coefs_shap)
print(count)
print(coefs_shap)

7
[0.       0.       0.00017  0.005245 0.015401 0.125622 0.003618 0.
 0.       0.       0.16366  0.       0.       0.       0.       0.
 0.       0.00037  0.       0.      ]


In [50]:

indices = np.argsort(-coefs_shap)[:count]
print(indices)

[10  5  4  3  6 17  2]


In [22]:
# pyexplainer explanation
os.system("jupyter nbextension enable --py widgetsnbextension")
print(py_example.keys())
explanation = pyExp.explain(py_example['X_explain'],py_example['y_explain'],search_function ='CrossoverInterpolation')
pyExp.visualise(explanation)

Enabling notebook extension jupyter-js-widgets/extension...
      - Validating: OK


dict_keys(['synthetic_data', 'synthetic_predictions', 'X_explain', 'y_explain', 'indep', 'dep', 'top_k_positive_rules', 'top_k_negative_rules', 'name', 'local_model'])


The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.


actual value of wmc < 0, currently do not support this type of rule


Output(layout=Layout(border='3px solid black'), outputs=({'output_type': 'display_data', 'data': {'text/plain'…

FloatSlider(value=58.0, continuous_update=False, description='#1 The value of wmc is less than 58', layout=Lay…

In [26]:
import re
def get_features_from_rules(rules):
    features = []
    for rule in rules['rule']:
        rule_feats = re.findall('[a-zA-Z]+',rule)
        features = features + rule_feats
    # print(features)
    return set(features)


In [112]:
top_rules = py_example['top_k_positive_rules'].head(9)
top_features_from_rules = get_features_from_rules(top_rules)
# print(top_features_from_rules)
# print(top_rules['rule'][::-1])
# print(top_rules['importance'])
prules = py_example['top_k_positive_rules'].head(9)
print(prules)

   index                                               rule  type      coef  \
0    244                            loc > 288.3450012207031  rule  0.154108   
1     85  rfc > 36.65500068664551 & loc > -1015.67004394...  rule  0.127445   
2     40                           rfc > 36.345001220703125  rule  0.127631   
3    234  cbo <= 242.58499908447266 & loc > 290.53500366...  rule  0.124233   
4    149  lcom > 75.5250015258789 & wmc > -15.2150006294...  rule  0.312035   
5    137  lcom > 70.25500106811523 & loc <= 262.60000610...  rule  0.443154   
6    186  noc <= 29.93000030517578 & wmc > -16.409999847...  rule  0.062352   
7     46  ic <= 2.365000009536743 & loc <= 284.330001831...  rule  0.064517   
8     24  wmc <= 3.024999976158142 & wmc <= 1.4700000286...  rule  0.112865   

    support  importance is_satisfy_instance  
0  0.788512    0.062932                True  
1  0.788512    0.052044                True  
2  0.793734    0.051643                True  
3  0.814621    0.048278  

Bad pipe message: %s [b'\xf6\xce\xad\t\xd0\x96$3\xc3\xc8\xf5\x82>\xab\xc1\xed)\x84 v\xff\xcc,\xfa\x0e\xdb\xed\xe1\xb7\xfcL]\x81\x1d\xdem\x95l\xbe\xec\xeb,T\xc0\xc3\xe2sZx\xd0\xcc\x00\x08\x13\x02\x13\x03\x13\x01\x00\xff\x01\x00\x00\x8f\x00\x00\x00\x0e\x00\x0c\x00\x00\t127.0.0.1\x00\x0b\x00\x04\x03\x00\x01\x02\x00']
Bad pipe message: %s [b'\x0c\x00\n\x00\x1d\x00\x17\x00\x1e']
Bad pipe message: %s [b"#\xd3\xcc\xe8\xfa\xbe\xdc\xefx\x84H\x05\x08|\x9a\xa0\xfaa \xbf\xd0\xb5\x18 \x1ac}\t\xf6[\xc2@G\xa4\xf8p\xb7'\xb6\xe9\x1d\xb4\x87\x91\xe5\x9a", b'\xde?\xb5\x00\x08\x13\x02\x13\x03\x13\x01\x00\xff\x01\x00\x00\x8f\x00\x00\x00\x0e\x00\x0c\x00\x00\t127.0.0.1\x00\x0b\x00\x04\x03\x00\x01\x02\x00\n\x00\x0c\x00\n\x00\x1d\x00\x17\x00\x1e\x00\x19\x00']
Bad pipe message: %s [b'#\x00\x00\x00\x16\x00\x00\x00\x17\x00\x00\x00\r\x00\x1e\x00\x1c\x04\x03\x05\x03\x06\x03']
Bad pipe message: %s [b'\x08\x08\x08\t\x08\n\x08', b'\x04\x08\x05\x08\x06\x04\x01\x05\x01\x06']
Bad pipe message: %s [b'']
Bad pipe message: 

In [87]:
boundaries = []
rule = "wmc > 36.65500068664551 & loc > -1015.6700439453125 & lcom >= -815.7749938964844"
rule2 = "rfc > 36.65500068664551"
props = rule.split(" & ")
# print(props)
for prop in props:
    sep = prop.split(" ")
    feat = sep[0]
    if "=" in sep[1]:
        value = float(sep[2])
    elif sep[1] == '>':
        value = np.ceil(float(sep[2]))
    elif sep[1] == '<':
        value = np.floor(float(sep[2]))
    boundaries.append((sep[0],value))
print(boundaries)

for criteria in boundaries:
    print(criteria[0])
features = list(features)
indices = [features.index(c[0]) for c in boundaries]
for i,ind in enumerate(indices):
    print(boundaries[i][1], ind)
# if > 36.677 or 36.2 : take val rounded up (take val -1)
# if >= 36.677 : take that val
# if < 36.67 or < 36.2 : take val rounded down

[('wmc', 37.0), ('loc', -1015.0), ('lcom', -815.7749938964844)]
wmc
loc
lcom
37.0 0
-1015.0 10
-815.7749938964844 5


In [79]:
features = X_test.columns
exp_feature_indices = [ i for i in range(len(features)) if features[i] in top_features_from_rules ]
print(exp_feature_indices)

[0, 2, 3, 4, 5, 10, 15]


In [34]:
exp_features = py_example['local_model'].get_rules().head(20).sort_values(by='importance',ascending=False)
print(exp_features.index[:10])


Int64Index([7, 6, 12, 3, 17, 2, 18, 5, 0, 14], dtype='int64')


Experiment

In [189]:
import os
import project
from project import Project 
import functions
from functions import *
import importlib

In [213]:
importlib.reload(functions)
from functions import *

In [36]:
project_names = ['ANT','CAMEL']
models = ['LR', 'SVM','KNN']



In [37]:
projects = {}
# prepare data for all 
for project_name in project_names:
    proj = Project(project_name)
    print(proj.name)
    proj.set_train_test()
    proj.prepare_data()
    projects[project_name] = proj
    for model in models:
        proj.train_global_model(model)
        # global_model = ant_project.models[model]
        
        

ANT


/anaconda/envs/xaienv/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


CAMEL


/anaconda/envs/xaienv/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:814: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [38]:
# METRIC 1 : local prediction fidelity
# get predictions for global, lime, pyexplainer, shap

df = pd.DataFrame()
for proj in projects:
    curr_project = projects[proj]
    X_train = curr_project.X_train
    y_train = curr_project.y_train

    for model in models:
        global_model = curr_project.models[model]
        
        limeExp,lime_explanations = get_explanations(curr_project, 'lime',model,X_train,y_train,global_model )
        pyExp,pyexplanations = get_explanations(curr_project, 'pyExp',model,X_train,y_train,global_model )
        shapExp,shap_explanations = get_explanations(curr_project, 'shap',model,X_train,y_train,global_model )

        lime_preds = [list(exp['rule'].local_pred.values())[0][0] for exp in lime_explanations] #lime local prediction probabilities
        global_preds = [exp['rule'].predict_proba[1] for exp in lime_explanations] #global pred probas
        py_preds = [exp['local_model'].predict_proba(exp['X_explain'].values)[0][1] for exp in pyexplanations]
        shap_preds = [shapExp.expected_value + sum(exp['shap_values']) for exp in shap_explanations]
        
        model_df = pd.DataFrame(prediction_fidelity(global_preds,lime_preds,py_preds,shap_preds))
        model_df['model'] = model
        model_df['project'] = proj
        df = pd.concat([df,model_df])

print(df)



X does not have valid feature names, but LogisticRegression was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


{'method': 'lime', 'mcc': 0.684952173827153, 'recall': 0.9473684210526315, 'precision': 0.7058823529411765}
{'method': 'pyExplainer', 'mcc': 0.8782526127038116, 'recall': 0.9736842105263158, 'precision': 0.8809523809523809}
{'method': 'shap', 'mcc': 0.8561706738324667, 'recall': 0.8157894736842105, 'precision': 1.0}


X does not have valid feature names, but SVC was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


{'method': 'lime', 'mcc': 0.9607843137254902, 'recall': 1.0, 'precision': 0.9607843137254902}
{'method': 'pyExplainer', 'mcc': 0.9801803569660552, 'recall': 0.9795918367346939, 'precision': 1.0}
{'method': 'shap', 'mcc': 0.9416057111088185, 'recall': 0.9387755102040817, 'precision': 1.0}


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


...

X does not have valid feature names, but SVC was fitted with feature names
Using 872 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


{'method': 'lime', 'mcc': 0.8164965809277261, 'recall': 1.0, 'precision': 0.8}
{'method': 'pyExplainer', 'mcc': 0.9385906354489059, 'recall': 0.925, 'precision': 1.0}
{'method': 'shap', 'mcc': 0.8987170342729172, 'recall': 0.875, 'precision': 1.0}


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
Using 872 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


{'method': 'lime', 'mcc': 0.0, 'recall': 0.0, 'precision': 0.0}
{'method': 'pyExplainer', 'mcc': 0.8362105717465858, 'recall': 1.0, 'precision': 0.7142857142857143}
{'method': 'shap', 'mcc': 1.0, 'recall': 1.0, 'precision': 1.0}
        method       mcc    recall  precision model
0         lime  0.684952  0.947368   0.705882    LR
1  pyExplainer  0.878253  0.973684   0.880952    LR
2         shap  0.856171  0.815789   1.000000    LR
0         lime  0.960784  1.000000   0.960784   SVM
1  pyExplainer  0.980180  0.979592   1.000000   SVM
2         shap  0.941606  0.938776   1.000000   SVM
0         lime  0.758522  0.878788   0.805556   KNN
1  pyExplainer  0.888015  0.939394   0.911765   KNN
2         shap  1.000000  1.000000   1.000000   KNN
0         lime  0.314183  0.552632   0.583333    LR
1  pyExplainer  0.852630  0.842105   0.969697    LR
2         shap  0.737468  0.657895   1.000000    LR
0         lime  0.816497  1.000000   0.800000   SVM
1  pyExplainer  0.938591  0.925000   1.0000

Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.


In [46]:
df['project'] = 'CAMEL'
df.iloc[:9,5] = 'ANT'
print(df)


        method       mcc    recall  precision model project
0         lime  0.684952  0.947368   0.705882    LR     ANT
1  pyExplainer  0.878253  0.973684   0.880952    LR     ANT
2         shap  0.856171  0.815789   1.000000    LR     ANT
0         lime  0.960784  1.000000   0.960784   SVM     ANT
1  pyExplainer  0.980180  0.979592   1.000000   SVM     ANT
2         shap  0.941606  0.938776   1.000000   SVM     ANT
0         lime  0.758522  0.878788   0.805556   KNN     ANT
1  pyExplainer  0.888015  0.939394   0.911765   KNN     ANT
2         shap  1.000000  1.000000   1.000000   KNN     ANT
0         lime  0.314183  0.552632   0.583333    LR   CAMEL
1  pyExplainer  0.852630  0.842105   0.969697    LR   CAMEL
2         shap  0.737468  0.657895   1.000000    LR   CAMEL
0         lime  0.816497  1.000000   0.800000   SVM   CAMEL
1  pyExplainer  0.938591  0.925000   1.000000   SVM   CAMEL
2         shap  0.898717  0.875000   1.000000   SVM   CAMEL
0         lime  0.000000  0.000000   0.0

In [50]:
# knn lime
camel = projects['CAMEL']
X_train = camel.X_train
y_train = camel.y_train
global_model = camel.models['KNN']
limeExp,lime_explanations = get_explanations(camel, 'lime','KNN',X_train,y_train,global_model )

print(lime_explanations[1])

--------------------------------------------------------------------------------


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names


--------------------------------------------------------------------------------


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names


--------------------------------------------------------------------------------


...

--------------------------------------------------------------------------------


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names


--------------------------------------------------------------------------------


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names


{'rule': <lime.explanation.Explanation object at 0x7f6ff3ee9490>, 'synthetic_instance_for_global_model': array([[22.        ,  2.        , 13.        , ...,  8.27272727,
         4.        ,  1.5       ],
       [ 2.93098935,  2.6828048 ,  0.        , ..., 11.11152154,
         0.82072763,  0.74481405],
       [ 7.41502888,  0.64303057, 12.17166145, ...,  6.6691704 ,
         2.        ,  0.82706166],
       ...,
       [ 4.99992155,  0.97597893,  0.        , ...,  5.86230741,
        12.65414117,  0.22409408],
       [11.11815675,  2.18384714,  0.        , ..., 17.64704074,
        13.30901028,  0.75563661],
       [ 2.27812543,  0.89133406,  0.        , ...,  2.2641996 ,
         0.99283539,  0.4726887 ]]), 'synthetic_instance_for_local_model': array([[1., 1., 1., ..., 1., 1., 1.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 1., ..., 1., 0., 0.],
       [1., 0., 1., ..., 1., 0., 1.],
       [0., 0., 1., ..., 0., 0., 0.]]), '

In [60]:
example = lime_explanations[4]['rule']
print(example.local_pred)

lime_preds = np.array([list(exp['rule'].local_pred.values())[0][0] for exp in lime_explanations])
print(lime_preds[lime_preds>0.5])
# metrics.precision_score(np.array(global_preds)>0.5,np.array(lime_preds)>0.5)

{1: array([0.42158278])}
[]


In [123]:
pyExp,pyexplanations = get_explanations(projects['ANT'], 'pyExp','KNN',X_train,y_train,global_model )
ex = pyexplanations[1]


In [126]:
e = ex['y_explain']
if e[0]==True:
    print(e)

name
org.apache.tools.ant.util.Watchdog    True
Name: defect, dtype: bool


In [151]:
# METRIC 2 : internal fidelity 

df = pd.DataFrame()
for proj in projects:
    curr_project = projects[proj]
    X_test = curr_project.X_test
    y_test = curr_project.y_test
    X_train = curr_project.X_train
    y_train = curr_project.y_train
    test_data_x,test_data_y,_ = curr_project.get_sampled_data()

    global_model = curr_project.models['LR']
    
    limeExp,lime_explanations = get_explanations(curr_project, 'lime',model,X_train,y_train,global_model )
    pyExp,pyexplanations = get_explanations(curr_project, 'pyExp',model,X_train,y_train,global_model )
    shapExp,shap_explanations = get_explanations(curr_project, 'shap',model,X_train,y_train,global_model )

    model_df = pd.DataFrame(internal_fidelity(global_model,test_data_x,test_data_y,lime_explanations,pyexplanations,shap_explanations))  
    recalls = model_df['recalls']
    model_df = model_df.iloc[:,:-1]
    model_df['model'] = model
    model_df['project'] = proj
    df = pd.concat([df,model_df])
print(df)
    


X does not have valid feature names, but LogisticRegression was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.
X does not have valid feature names, but LogisticRegression was fitted with feature names
Using 872 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


        method  avg_recall model project
0         LIME       0.422   SVM     ANT
1  PyExplainer       0.459   SVM     ANT
2         SHAP       1.000   SVM     ANT
0         LIME       0.411   SVM   CAMEL
1  PyExplainer       0.519   SVM   CAMEL
2         SHAP       1.000   SVM   CAMEL


In [192]:
# METRIC 3 : faithfulness
df = pd.DataFrame()
for proj in projects:
    curr_project = projects[proj]
    X_train = curr_project.X_train
    y_train = curr_project.y_train
    test_data_x,test_data_y,_ = curr_project.get_sampled_data()

    for model in models:
        global_model = curr_project.models[model]
        
        limeExp,lime_explanations = get_explanations(curr_project, 'lime',model,X_train,y_train,global_model )
        pyExp,pyexplanations = get_explanations(curr_project, 'pyExp',model,X_train,y_train,global_model )
        shapExp,shap_explanations = get_explanations(curr_project, 'shap',model,X_train,y_train,global_model )

        model_df = pd.DataFrame(faithfulness(global_model, test_data_x, lime_explanations, pyexplanations, shap_explanations))
        faithfulness_scores = model_df['faithfulness_scores']
        model_df = model_df.iloc[:,:-1]
        model_df['model'] = model
        model_df['project'] = proj
        df = pd.concat([df,model_df])

print(df)

X does not have valid feature names, but LogisticRegression was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid fe

        method  avg_faithfulness model project
0         LIME          0.280712    LR     ANT
1         SHAP          0.178263    LR     ANT
2  pyExplainer         -0.118601    LR     ANT
0         LIME         -0.051180   SVM     ANT
1         SHAP               NaN   SVM     ANT
2  pyExplainer               NaN   SVM     ANT
0         LIME               NaN   KNN     ANT
1         SHAP               NaN   KNN     ANT
2  pyExplainer               NaN   KNN     ANT
0         LIME          0.036057    LR   CAMEL
1         SHAP          0.269337    LR   CAMEL
2  pyExplainer         -0.002525    LR   CAMEL
0         LIME         -0.243338   SVM   CAMEL
1         SHAP          0.294841   SVM   CAMEL
2  pyExplainer         -0.067188   SVM   CAMEL
0         LIME               NaN   KNN   CAMEL
1         SHAP               NaN   KNN   CAMEL
2  pyExplainer               NaN   KNN   CAMEL


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with fe

In [197]:
# METRIC 4 : monotonicity
df = pd.DataFrame()
for proj in projects:
    curr_project = projects[proj]
    X_train = curr_project.X_train
    y_train = curr_project.y_train
    test_data_x,test_data_y,_ = curr_project.get_sampled_data()

    for model in models:
        global_model = curr_project.models[model]
        
        limeExp,lime_explanations = get_explanations(curr_project, 'lime',model,X_train,y_train,global_model )
        pyExp,pyexplanations = get_explanations(curr_project, 'pyExp',model,X_train,y_train,global_model )
        shapExp,shap_explanations = get_explanations(curr_project, 'shap',model,X_train,y_train,global_model )

        model_df = pd.DataFrame(monotonicity(global_model, test_data_x, lime_explanations, pyexplanations, shap_explanations))
        monotonicity_scores = model_df['monotonicity_scores']
        model_df = model_df.iloc[:,:-1]
        model_df['model'] = model
        model_df['project'] = proj
        df = pd.concat([df,model_df])

print(df)

X does not have valid feature names, but LogisticRegression was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid fe

10
20
10
19
10
18
10
16
10
20
10
18
10
19
10
18
10
17
10
19
10
18
10
15
10
18
10
19
10
18
10
15
10
18
10
15
10
19
10
13
10
16
10
17
10
20
10
19
10
19
10
19


X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not

10
15
10
20
10
19
10
20
10
18
10
19
10
18
10
14
10
19
10
18
10
19
10
13
10
20
10
17
10
20
10
19
10
17
10
20
10
18
10
19
10
16
10
20
10
15
10
20
10
12
10
16


X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not

...

X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with fe

10
16
10
16
10
11
10
17
10
10
10
11
10
8
10
13


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with fe

10
12
10
11
10
17
10
11
10
15
10
17
10
12
        method  total_monotonicity model project
0         LIME                   0    LR     ANT
1         SHAP                   1    LR     ANT
2  pyExplainer                   0    LR     ANT
0         LIME                   0   SVM     ANT
1         SHAP                  57   SVM     ANT
2  pyExplainer                  19   SVM     ANT
0         LIME                  66   KNN     ANT
1         SHAP                  80   KNN     ANT
2  pyExplainer                   5   KNN     ANT
0         LIME                   2    LR   CAMEL
1         SHAP                   1    LR   CAMEL
2  pyExplainer                   0    LR   CAMEL
0         LIME                   0   SVM   CAMEL
1         SHAP                   6   SVM   CAMEL
2  pyExplainer                   0   SVM   CAMEL
0         LIME                  25   KNN   CAMEL
1         SHAP                  33   KNN   CAMEL
2  pyExplainer                   2   KNN   CAMEL


X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
X does not have valid feature names, but KNeighborsClassifier was fitted with fe

In [198]:
print(df)

        method  total_monotonicity model project
0         LIME                   0    LR     ANT
1         SHAP                   1    LR     ANT
2  pyExplainer                   0    LR     ANT
0         LIME                   0   SVM     ANT
1         SHAP                  57   SVM     ANT
2  pyExplainer                  19   SVM     ANT
0         LIME                  66   KNN     ANT
1         SHAP                  80   KNN     ANT
2  pyExplainer                   5   KNN     ANT
0         LIME                   2    LR   CAMEL
1         SHAP                   1    LR   CAMEL
2  pyExplainer                   0    LR   CAMEL
0         LIME                   0   SVM   CAMEL
1         SHAP                   6   SVM   CAMEL
2  pyExplainer                   0   SVM   CAMEL
0         LIME                  25   KNN   CAMEL
1         SHAP                  33   KNN   CAMEL
2  pyExplainer                   2   KNN   CAMEL


In [214]:
# METRIC 5 : uniqueness
df = pd.DataFrame()
for proj in projects:
    curr_project = projects[proj]
    X_train = curr_project.X_train
    y_train = curr_project.y_train
    test_data_x,test_data_y,_ = curr_project.get_sampled_data()

    for model in models:
        global_model = curr_project.models[model]
        
        limeExp,lime_explanations = get_explanations(curr_project, 'lime',model,X_train,y_train,global_model )
        pyExp,pyexplanations = get_explanations(curr_project, 'pyExp',model,X_train,y_train,global_model )
        shapExp,shap_explanations = get_explanations(curr_project, 'shap',model,X_train,y_train,global_model )

        model_df = pd.DataFrame(uniqueness(global_model,test_data_x, lime_explanations, pyexplanations, shap_explanations))
        uniqueness_scores = model_df['uniqueness']
        model_df['model'] = model
        model_df['project'] = proj
        df = pd.concat([df,model_df])

print(df)

X does not have valid feature names, but LogisticRegression was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid fe

('rfc > 62.00', 0.5315085907352262)
     index                                               rule  type      coef  \
0      662  rfc > 40.915000915527344 & dit <= 4.0050001144...  rule  0.124302   
1       91  rfc > 43.420000076293945 & max_cc <= 13.855000...  rule  0.099401   
2      905  rfc > 40.875 & amc > -11.125 & dit <= 5.634999...  rule  0.116516   
3      184                          dit <= 1.9550000429153442  rule  0.095225   
4      496  wmc <= 25.925000190734863 & rfc <= 60.02000045...  rule  0.083513   
..     ...                                                ...   ...       ...   
158    655  dam <= 0.9449999928474426 & max_cc > 22.879999...  rule  0.002911   
159    295  lcom <= 99.74499893188477 & rfc <= 52.57999992...  rule  0.000797   
160    899  avg_cc > 2.4350000619888306 & avg_cc > 2.74500...  rule  0.002062   
161    172  wmc <= 2.7300000190734863 & dit <= 3.529999971...  rule  0.002310   
162    144   rfc > 40.03000068664551 & ic > 3.325000047683716  rule  0.00

X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not

     index                                               rule  type      coef  \
0      287  max_cc <= 5.664999961853027 & max_cc <= 19.324...  rule  0.604064   
1      528                            rfc > 41.89999961853027  rule  0.371530   
2      609  dit <= 2.3149999380111694 & rfc <= 52.05500030...  rule  0.344771   
3      694  rfc > 43.44000053405762 & ce > -5.789999961853027  rule  0.334440   
4      801  rfc > 30.074999809265137 & dit <= 1.5449999570...  rule  0.327365   
..     ...                                                ...   ...       ...   
158    411  max_cc > 20.55500030517578 & ce > 0.9050000011...  rule  0.016914   
159    471                          rfc <= 29.050000190734863  rule  0.001979   
160    671                            rfc > 31.84500026702881  rule  0.001000   
161    312                           rfc > 31.899999618530273  rule  0.001000   
162    634  ce > 5.295000076293945 & max_cc > 4.9500000476...  rule  0.000679   

      support  importance i

X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not have valid feature names, but LogisticRegression was fitted with feature names
X does not

     index                                               rule  type      coef  \
0       39  dit <= 5.744999885559082 & amc > 23.9300003051...  rule  0.278705   
1      694  cam > 0.1850000023841858 & dit > 2.28499996662...  rule  0.282739   
2      117  rfc > 29.755000114440918 & max_cc <= 3.3149999...  rule  0.282358   
3      472  loc <= 237.77999877929688 & amc > -28.27999877...  rule  0.352320   
4      792  dit <= 5.759999990463257 & ce > 7.470000028610...  rule  0.203036   
..     ...                                                ...   ...       ...   
150    193  rfc <= 54.314998626708984 & dit > 2.9950000047...  rule  0.003696   
151    490  dit <= 3.15500009059906 & amc <= 5.24000000953...  rule  0.007501   
152    561  amc <= 23.954999923706055 & max_cc <= 13.95499...  rule  0.002485   
153    325  amc <= 9.365000009536743 & amc <= 31.189999580...  rule  0.006475   
154     25  rfc > 40.045000076293945 & noc <= 0.9149999916...  rule  0.000022   

      support  importance i

X does not have valid feature names, but SVC was fitted with feature names
Using 351 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names
X does not have valid feature names, but SVC was fitted with feature names


('loc > 543.00', 0.3199269715652106)
     index                                               rule  type      coef  \
0      509  loc > 269.3300018310547 & rfc > 22.54500007629...  rule  0.370044   
1      380                            loc > 302.8699951171875  rule  0.250578   
2      157                             loc > 302.635009765625  rule  0.250578   
3      400  loc > 260.14500427246094 & rfc > 9.15499997138977  rule  0.236371   
4      129  rfc > 11.419999837875366 & loc > 263.119995117...  rule  0.167401   
..     ...                                                ...   ...       ...   
162     78  loc > 259.64500427246094 & loc <= 262.36999511...  rule  0.006324   
163    826  max_cc > 2.3600000143051147 & mfa > 1.23000001...  rule  0.002241   
164    601  ce <= 17.69499969482422 & noc > 4.315000057220459  rule  0.000086   
165    868  rfc > 48.30500030517578 & mfa <= -0.1300000026...  rule  0.000022   
166    377  mfa > 1.1850000023841858 & dam > 1.125 & max_c...  rule  0.0

KeyError: 0